# Processing the SMAGs DB published by [Delmont et.al. 2020](https://www.biorxiv.org/content/10.1101/2020.10.15.341214v2):  
**Excerpt from abstract:**  
We used 280 billion Tara Oceans metagenomic reads from polar, temperate, and tropical sunlit oceans to reconstruct and manually curate more than 700 abundant and widespread eukaryotic environmental genomes ranging from 10 Mbp to 1.3 Gbp. This genomic resource covers a wide range of poorly characterized eukaryotic lineages that complement long-standing contributions from culture collections while better representing plankton in the upper layer of the oceans.  

### The DB is accessible from [TARA Oceans repository](https://www.genoscope.cns.fr/tara/).  

**The goal here is:**  
To properly format this protein seq DB in a way that one can use it with humann to profile environmental samples at the metabolic pathway level. To achieve this, we have to: 

    1. Scoop out sequences that can be taxonomically associated with an NCBI taxID down to the genus level, or at least the family level (using BioPython here!).
    2. Make sure that a given sequence is sufficiently large, e.g. seq-len > 80 AA.
    3. Annotate the target sequence against UniRef90_2020-2.
    4. Create a .dmnd DB out of this newly created .faa file of UniRef90 annotated sequences.
    
Jayson Gutierrez: 10/01/2022

In [1]:
import matplotlib
%matplotlib inline
import matplotlib.pyplot as plt
from matplotlib import cm
import seaborn as sns

from subprocess import Popen, call, STDOUT, PIPE
import os
import shutil
import pandas as pd
import numpy as np
import matplotlib
import json
import glob
import re
import gzip
import sys
import csv
import time
import io
import pathlib

import itertools

import json
import urllib.request

import Bio.SeqIO as bioseqio
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord
#from Bio.Alphabet import IUPAC
from Bio import Entrez

from ete3 import NCBITaxa
from taxonomy_ranks import TaxonomyRanks

from IPython.display import Image

import warnings
warnings.filterwarnings('ignore')

import urllib
from collections import OrderedDict 

import fastaparser

In [2]:
!which python

/home/VLIZ2000/jayson.gutierrez/anaconda3/envs/bioinformatics/bin/python


In [3]:
matplotlib.rcParams['savefig.dpi'] = 900
matplotlib.rcParams['figure.dpi'] = 600
sns.set_style("whitegrid", {'axes.grid' : False})
sns.set_context("paper")
sns.set(font='serif')
# sns.set_style("white", {
#         "font.family": "serif",
#         "font.serif": ["Times", "Palatino", "serif"]
#     })
sns.set_style('ticks')

In [4]:
from utilities import *

In [5]:
def entry_filter(tax_ranks):
    '''Function to filter taxonomic ranks in the SMAGs metadata'''
    gr, fr, orr, cr = tax_ranks
    if( (isinstance(gr,str)) and ('_' not in gr) and ('-' not in gr)):
        return gr
    elif( (isinstance(fr,str)) and ('_' not in fr) and ('-' not in fr)):
        return fr
    elif( (isinstance(orr,str)) and ('_' not in orr) and ('-' not in orr)):
        return orr
    elif( (isinstance(cr,str)) and ('_' not in cr) and ('-' not in cr)):
        return cr
    else:
        return 'NA'

def orgn2taxranks(tax_ranks,best_tax_g2taxlvls):
    '''Utility to map the computed tax ranks corresponding to a given entry in the SMAGs metadata'''
    gr, fr, orr, cr = tax_ranks
    if(gr in best_tax_g2taxlvls.keys()):
        return best_tax_g2taxlvls[gr]
    elif(fr in best_tax_g2taxlvls.keys()):
        return best_tax_g2taxlvls[fr]
    elif(orr in best_tax_g2taxlvls.keys()):
        return best_tax_g2taxlvls[orr]
    elif(cr in best_tax_g2taxlvls.keys()):
        return best_tax_g2taxlvls[cr]
    else:
        return 'NA'

def modify_TOSAG_labels(s):
    '''Utility to modify entries with TOSAG substring'''
    if('TOSAG' in s): 
        return s.split('TOSAG')[0] + 'TOSAG' + s.split('TOSAG')[1].replace("_","-")
    else:
        return s    

def make_fasta_header_templ(orgs_list):
    '''Function that takes in a list of organisms and query the ncbi taxid in order to fetch the 
       taxonomic range and tax id down to the genus level. 
       The function receives a list of organism names (orgs_list) and returns a dict (best_tax_g2taxlvls)
    '''
    best_tax_g2taxlvls = {}
    for g in orgs_list:
        if(g not in best_tax_g2taxlvls.keys()):
            #Format tax ranks for fasta headers
            try:
                rank_taxon = TaxonomyRanks(g)
                rank_taxon.get_lineage_taxids_and_taxanames()
                rank_dict = list(rank_taxon.lineages.values())[0]

                #Fetch tax ranks in a given order for formatting fasta headers according to humann
                gfo_ranks = []
                for rrt in ['genus','species','class','order','family']:
                    txn = rank_dict[rrt][0]
                    if(txn=='NA'):
                        gfo_ranks.append('unclassified')
                    else:
                        gfo_ranks.append(txn)

                #Check for NCBI tax IDs (favoring lower ranks)
                if(rank_dict['genus'][1]!='NA'):
                    ncbi_txid = rank_dict['genus'][1]
                elif(rank_dict['family'][1]!='NA'):
                    ncbi_txid = rank_dict['family'][1]
                elif(rank_dict['order'][1]!='NA'):
                    ncbi_txid = rank_dict['order'][1]
                elif(rank_dict['class'][1]!='NA'):
                    ncbi_txid = rank_dict['class'][1]
                else:
                    ncbi_txid = 'NA'

                #Add ncbi taxid
                gfo_ranks.insert(2,ncbi_txid)
                #Update dict
                best_tax_g2taxlvls[g] =  "UniRef90|SeqLen|g__{}.s__{}|{}|c__{}.o__{}.f__{}".format(*gfo_ranks)    

            except:
                pass
           
    #Then filter out those cases for which taxID are NA
    new_best_tax_g2taxlvls = dict()
    # Iterate over all the items in dictionary and filter items which has even keys
    for (key, value) in best_tax_g2taxlvls.items():
       # Check if key is even then add pair to new dictionary
       if ('|NA|' not in value):
        new_best_tax_g2taxlvls[key] = value
        
    return new_best_tax_g2taxlvls

In [6]:
#For searches over NCBI, let them know who you are in advance!
Entrez.email = 'jayson.gutierrez@vliz.be'

### Loading metadata on SMAGs

In [435]:
fid = 'data/Delmont_etal_2020_Table-3.tsv'
smags_meta_df = pd.read_csv(fid,sep='\t')
#Filtering out entries that correspond to METDB, which lack any representation in the original fasta file SMAGs_v1_concat.faa.tar.gz 
smags_meta_df = smags_meta_df[~smags_meta_df['Genome_Id final names'].str.contains("METDB")]
print("Number of entries in filtered metadata: {}".format(smags_meta_df.shape[0]))
#Filter df according to genre column: keep only those for which genus name is not NA
#smags_meta_df = smags_meta_df[smags_meta_df["Best_taxonomy_GENRE"].apply(lambda s: isinstance(s,str))]
smags_meta_df.head().T

Number of entries in filtered metadata: 713


0                         1  \
Genome_Id final names     TARA_ANE_2018_MAG_00101     TARA_AON_82_MAG_00012   
Genome_Id (beta-version)       TARA_ANE_MAG_00101     TARA_AON_82_MAG_00012   
Niche_identification                          Yes                        No   
METDB_match_98percent                         NaN               METDB_00284   
METDB_taxonomy                                NaN  Ostreococcus lucimarinus   
...                                           ...                       ...   
Mean_Phos                                0.342148                       NaN   
Mean_Sal                                    35.61                       NaN   
Mean_Si                                   2.96717                       NaN   
Mean_SI_NO3                              0.324497                       NaN   
Mean_T                                    16.6772                       NaN   

                                              2                      3  \
Genome_Id final names     TARA_AON_82_MAG_00097  TARA_AON_82_MAG_00118   
Genome_Id (beta-version)  TARA_AON_82_MAG_00097  TARA_AON_82_MAG_00118   
Niche_identification                         No                     No   
METDB_match_98percent                       NaN            METDB_00258   
METDB_taxonomy                              NaN     Micromonas pusilla   
...                                         ...                    ...   
Mean_Phos                                   NaN                    NaN   
Mean_Sal                                    NaN                    NaN   
Mean_Si                                     NaN                    NaN   
Mean_SI_NO3                                 NaN                    NaN   
Mean_T                                      NaN                    NaN   

                                              4  
Genome_Id final names     TARA_AON_82_MAG_00125  
Genome_Id (beta-version)  TARA_AON_82_MAG_00125  
Niche_identification                        Yes  
METDB_match_98percent                       NaN  
METDB_taxonomy                              NaN  
...                                         ...  
Mean_Phos                              0.336298  
Mean_Sal                                36.2385  
Mean_Si                                 2.79687  
Mean_SI_NO3                            0.177992  
Mean_T                                  18.4071  

[88 rows x 5 columns]

Let's filter entries in df based on some criteria, and create a dict mapping genre names to a humann-compatible template for the fasta header

In [567]:
#Fetch list of genre reported in the study
cols2search = ['Best_taxonomy_GENRE','Best_taxonomy_FAMILY','Best_taxonomy_ORDER','Best_taxonomy_CLASS']
orgs_list = smags_meta_df[cols2search].apply(entry_filter,axis=1).value_counts().index.values
orgs_list = list(filter(lambda s: s!='NA',orgs_list))
len(orgs_list)

56

In [534]:
#Make dict mapping genus name to tax ranks
best_tax_g2taxlvls = make_fasta_header_templ(orgs_list)
print("Total number of species in the SMAGs DB with NCBI taxonomic association at least at the class level: {}".format(str(len(best_tax_g2taxlvls))))

Total number of species in the SMAGs DB with NCBI taxonomic association at least at the class level: 49


Let's peek at the dict created above

In [552]:
for (n,item) in enumerate(best_tax_g2taxlvls.items()):
    print("{}: {}".format(*item))
    if(n>20): break

Hexanauplia: UniRef90|SeqLen|g__unclassified.s__unclassified|72037|c__Hexanauplia.o__unclassified.f__unclassified
Chrysochromulinaceae: UniRef90|SeqLen|g__unclassified.s__unclassified|1136790|c__unclassified.o__Prymnesiales.f__Chrysochromulinaceae
Oikopleuridae: UniRef90|SeqLen|g__unclassified.s__unclassified|41302|c__Appendicularia.o__Copelata.f__Oikopleuridae
Phaeocystis: UniRef90|SeqLen|g__Phaeocystis.s__unclassified|33656|c__unclassified.o__Phaeocystales.f__Phaeocystaceae
Chrysophyceae: UniRef90|SeqLen|g__unclassified.s__unclassified|2825|c__Chrysophyceae.o__unclassified.f__unclassified
Micromonas: UniRef90|SeqLen|g__Micromonas.s__unclassified|38832|c__Mamiellophyceae.o__Mamiellales.f__Mamiellaceae
Bicosoecales: UniRef90|SeqLen|g__unclassified.s__unclassified|33651|c__Bigyra.o__Bicosoecida.f__unclassified
Choreotrichida: UniRef90|SeqLen|g__unclassified.s__unclassified|200605|c__Spirotrichea.o__Choreotrichida.f__unclassified
Bacillariaceae: UniRef90|SeqLen|g__unclassified.s__unclass

In [616]:
#Here we filter entries for which NCBI taxID was found at least down to the class level
smags_tax_ranks_df = smags_meta_df[cols2search]
filtered_smags_meta_df = smags_meta_df[smags_tax_ranks_df.apply(lambda l: any([i in best_tax_g2taxlvls.keys() for i in list(map(str,l))]),axis=1)]

#Next we add the header template corresponding to each entry, which will be used to correctly label each seq entry in SMAGs_v1_concat.faa.tar.gz
pd.options.mode.chained_assignment = None
header_templates = filtered_smags_meta_df[cols2search].apply(lambda l: orgn2taxranks(l, best_tax_g2taxlvls), axis=1)
filtered_smags_meta_df["Humann_header_template"] = header_templates
#Modify entries labelled with TOSAG substring to properly query fasta file
filtered_smags_meta_df["Genome_Id final names"] = filtered_smags_meta_df["Genome_Id final names"].apply(modify_TOSAG_labels)

In [621]:
#Check the top 10 most abundant groups or organims in the SMAGs DB
print("Most widely represented groups in the SMAGs DB:")
filtered_smags_meta_df["Humann_header_template"].value_counts().iloc[:10]

Most widely represented groups in the SMAGs DB:


UniRef90|SeqLen|g__unclassified.s__unclassified|72037|c__Hexanauplia.o__unclassified.f__unclassified               215
UniRef90|SeqLen|g__unclassified.s__unclassified|1136790|c__unclassified.o__Prymnesiales.f__Chrysochromulinaceae     39
UniRef90|SeqLen|g__unclassified.s__unclassified|41302|c__Appendicularia.o__Copelata.f__Oikopleuridae                37
UniRef90|SeqLen|g__Phaeocystis.s__unclassified|33656|c__unclassified.o__Phaeocystales.f__Phaeocystaceae             27
UniRef90|SeqLen|g__unclassified.s__unclassified|2825|c__Chrysophyceae.o__unclassified.f__unclassified               23
UniRef90|SeqLen|g__Micromonas.s__unclassified|38832|c__Mamiellophyceae.o__Mamiellales.f__Mamiellaceae               20
UniRef90|SeqLen|g__unclassified.s__unclassified|33651|c__Bigyra.o__Bicosoecida.f__unclassified                      16
UniRef90|SeqLen|g__unclassified.s__unclassified|200605|c__Spirotrichea.o__Choreotrichida.f__unclassified            15
UniRef90|SeqLen|g__unclassified.s__unclassified|

### Query original SMAGs DB and scoop out sequences for particular samples, which are dumped into a another fasta file

In [638]:
# data_dir = '/home/VLIZ2000/jayson.gutierrez/meta_omics_data/marine_databases/TARA_Oceans/TARA_SMAGs/'
# fasta_fid = os.path.join(data_dir,"SMAGs_v1_concat.faa.tar.gz")
# new_fasta_fid = os.path.join(data_dir,"SMAGs_v1_concat_filtered.faa")
# #Set minimal seq len threshold
# seq_len_thr = 90

# #Loop over DB
# with gzip.open(fasta_fid, "rt") as handle:
#     #Loop over seq DB
#     for record in bioseqio.parse(handle, "fasta"):
#         fasta_id = record.description
#         query_tag = "_".join(fasta_id.split("_")[:-1])
#         #Get corresponding sample metadata
#         sample_metadata = filtered_smags_meta_df[filtered_smags_meta_df["Genome_Id final names"].str.contains(query_tag)]
#         #Replace current header with a new one for diamond annotation against UniRef
#         if(len(sample_metadata)==1):
#             record_len = len(record.seq)
#             #Check whether the query seq meets the following criteria
#             if(record_len>=seq_len_thr):
#                 #Replace fasta header and modify accordingly
#                 #NOTE: this provides a template for the diamond annotation against UniRef90 DB
#                 seq_header_temp = sample_metadata['Humann_header_template'].iloc[0].replace('UniRef90',fasta_id)
#                 new_seq_header = seq_header_temp.replace("SeqLen",str(record_len*3))
#                 record.id = ''
#                 record.name = ''
#                 record.description = ''
#                 record.id = new_seq_header
#                 #Dump record into file
#                 with open(new_fasta_fid, "a") as output_handle:
#                     bioseqio.write(record, output_handle, "fasta")       

In [657]:
!head $data_dir/SMAGs_v1_concat_filtered.faa

>Metagenome_centric_SAG_TOSAG00-12_Gene2|876|g__unclassified.s__unclassified|33651|c__Bigyra.o__Bicosoecida.f__unclassified
MKVDIENTPEVIFRIHKSSCDRRRIPKRASIPVMRICRCVCFRVVTGSCDVTTTRDGDSE
TLGGTFTLEFEGQRTGYLPYDISADDMKTALELLDTVGEVDVSRSDADENSGYVWSVTFL
TDLGNLNTMVADGRSLMGTVPIITIHENDGTSPPFNSGVGGPALGSETYTDLDSTPMSYR
IDGHEQGVPYYVRVAATNAIGYGEALLATPRNEIPLSGTSANSHVRSHSLSFTAIHSPSR
FQCTHNALIRRGHETEPIEYNAADSTVKRRLEELPNVGTVTVNRVQTYIDE*
>Metagenome_centric_SAG_TOSAG00-12_Gene3|1248|g__unclassified.s__unclassified|33651|c__Bigyra.o__Bicosoecida.f__unclassified
MSSFRGLLQHQRGFKSFTFRTTKTRFSGSILRRRMCTGKKKVEDEAKKKLEEEASNASVP
HLILGMAAGVGGSWLGLGMFGGAIYLTSSFGDNAFAGRLQALLLLGTFVFPPVVGAVAWA
YVIQAEWGIGFFLTSTGLFYGVPVLTYMNVLKESGESISETREKRLKLLMNLNHTDLSNL


<br>

### Processing output files from the functional annotation of the SMAGs DB against the UniRef90 catalog via Diamond  
Diamond was run with the following settings --evalue 1e-3 --query-cover 80 --id 50

In [7]:
#Numeric columns in output files
new_col_names = ['Percentage_of_identical_matches', 'Alignment_length', 'Number_of_mismatches', 'Number_of_gap_openings',
                 'Start_of_alignment_in_query', 'End_of_alignment_in_query','Start_of_alignment_in_subject', 
                 'End_of_alignment_in_subject','Expected_value', 'Bit_score']

In [8]:
annotat_files = glob.glob('data/SMAGs_filtered_chunk_annots_*.tsv')
sorted_annotat_files = sorted(annotat_files, key = lambda s: int(os.path.basename(s).split("_")[-1].replace(".tsv","")))

In [9]:
#Loop over all the annotation results files
annot_res_df_cont = []
for af in sorted_annotat_files:
    with open(af,"r") as annot_file:
        lines = annot_file.readlines()

    col_names = [s.replace(" ","_") for s in lines[2].split(":")[1].strip().split(', ')]

    #Fetch entries
    annot_res = []
    for l in lines[3:]:
        annot_res.append(l.strip().split('\t'))

    #Cast raw data into a DF
    annot_res_df = pd.DataFrame(data=annot_res,columns=col_names)

    #Convert fields to numeric and cast data as new DF
    new_annot_res_df = annot_res_df[new_col_names].apply(pd.to_numeric)
    new_annot_res_df["Subject_ID"] = annot_res_df["Subject_ID"]
    new_annot_res_df.index = annot_res_df["Query_ID"]
    #Stack up DFs
    annot_res_df_cont.append(new_annot_res_df)    

In [10]:
#Create full df of annotations
annot_all_results_df = pd.concat(annot_res_df_cont)
print("Total number of sequences: {}".format(annot_all_results_df.shape[0]))
print("Number of distinct organisms in the filtered SMAGs DB:")
annot_all_results_df.index.map(lambda s : s.split("|")[3]).value_counts().shape[0]

Total number of sequences: 1603852
Number of distinct organisms in the filtered SMAGs DB:


47

In [ ]:
#Iterate over DF rows to generate a new col with the definitive UniRef90-based annotation for a given seq in the SMAGs DB
new_uniref_annots = []
for df in annot_all_results_df.iterrows():
    #Fetch original fields from header
    origanot,seql,maintxnl,ncbitxid,extratax = df[0].split("|")
    #Fetch UniRef90 annotation derived from diamond run
    uniref_annot = df[1]['Subject_ID']
    new_uniref_annots.append("{}|{}|{}__{}|{}".format(uniref_annot,seql,maintxnl,ncbitxid,extratax))
    
annot_all_results_df["UniRef90_Annotation"] = new_uniref_annots

In [ ]:
#Many potentially redundant seqs
annot_all_results_df["UniRef90_Annotation"].value_counts()

### Formatting seq headers in a humann-compatible way

In [16]:
#Set input/output files
seq_hits_files = glob.glob(os.path.join(data_dir,'SMAGs_filtered_chunk_annot_seqs_*.faa'))
sorted_seq_hits_files = sorted(seq_hits_files, key = lambda s: int(os.path.basename(s).split("_")[-1].replace(".faa","")))
SMAGs_uniref90_annotated_fid = os.path.join(data_dir,"SMAGs_UniRef90_Annotated.faa")

# #Now loop over each subset of annotated seqs and dump them into a file with appropriate header
# #A list to store non-redundant headers
# new_header_cont = []
# for seqs_subset in sorted_seq_hits_files:
#     #Now, let's iterate over the seqs with hits on UniRef90
#     with open(seqs_subset,"r") as handle:
#         for (i,record) in enumerate(bioseqio.parse(handle, "fasta")):
#             try:
#                 new_header = annot_all_results_df.loc[record.description]["UniRef90_Annotation"]
#                 #Make sure that X is not part of the seq and that the seq has not been previously dumped into the fasta file
#                 if("X" not in record.seq):
#                     if(new_header in new_header_cont):
#                         pass
#                     else:
#                         #Update list
#                         new_header_cont.append(new_header)
#                         #Update header
#                         record.id = ''
#                         record.name = ''
#                         record.description = ''
#                         record.id = new_header
#                         #Dump record into file
#                         with open(SMAGs_uniref90_annotated_fid, "a") as output_handle:
#                             bioseqio.write(record, output_handle, "fasta")
#             except:
#                 pass

In [25]:
!grep -c '>' $SMAGs_uniref90_annotated_fid

965400


### Merging together two DBs: initially created and SMAGs

In [78]:
# #Filtered SMAGs seqs
# SMAGs_uniref90_annotated_fid = '/home/VLIZ2000/jayson.gutierrez/meta_omics_data/marine_databases/TARA_Oceans/TARA_SMAGs/SMAGs_UniRef90_Annotated.faa'
# #Initial DB built from > 100 genomes
# inital_db = '/data/home/VLIZ2000/jayson.gutierrez/meta_omics_data/marine_databases/Struo/UniRefAnnotEukGeneSeqs/checked_assembly_clustered_rep_seq.fasta'
# target_dbs = [inital_db, SMAGs_uniref90_annotated_fid]
# #Dump files into this new fasta file
# merged_fasta_fid = "/home/VLIZ2000/jayson.gutierrez/meta_omics_data/marine_databases/CustomProkEukDB/prok_euk_plankt_db_v1.0.faa"

In [72]:
# #Store taxIDs here
# ncbi_taxids = []
# for fid in target_dbs:
#     with open(fid,"r") as input_handle:
#         for (i,record) in enumerate(bioseqio.parse(input_handle, "fasta")):
#             with open(merged_fasta_fid, "a") as output_handle:
#                 bioseqio.write(record, output_handle, "fasta")
#             #Count number of different tax IDs
#             check4taxid = record.description.split("|")[2].split("__")[-1]
#             if(check4taxid.isnumeric() and (check4taxid not in ncbi_taxids)):
#                 ncbi_taxids.append(check4taxid)

In [79]:
# #Total number of sequences in DB version 1.0
# !grep -c '>' $merged_fasta_fid

2131295


### Making a DF describing taxonomic levels in DB created above

In [104]:
# tax_ranks = ['superkingdom','kingdom','class','order','family','genus']
# tax_ranks_cont = []
# for g in ncbi_taxids:
#     try:
#         rank_taxon = TaxonomyRanks(g)
#         rank_taxon.get_lineage_taxids_and_taxanames()
#         rank_dict = list(rank_taxon.lineages.values())[0]
#         ranks_comput = [rank_dict[k][0] for k in tax_ranks]
#         ranks_comput.insert(0,g)
#         tax_ranks_cont.append(ranks_comput)
#     except:
#         pass

# tax_ranks.insert(0,"taxID")
# #DF describing full range of taxonomic levels covered in our custom DB
# tax_ranks_df = pd.DataFrame(tax_ranks_cont,columns=tax_ranks)    

In [240]:
# new_col = tax_ranks_df.iloc[:,1:].apply(lambda s:"_".join(s),axis=1)
# tax_ranks_df["JoinedTaxLvls"] = new_col
# print("Summary of super-kingdoms: ")
# tax_ranks_df.drop_duplicates(subset=['JoinedTaxLvls'])["superkingdom"].value_counts()

Summary of super-kingdoms: 


Eukaryota    282
Bacteria      68
Archaea        1
Name: superkingdom, dtype: int64

Visualize family representation across DB

In [147]:
# sns.set_color_codes("pastel")
# x = tax_ranks_df["family"].value_counts().index.values
# y = tax_ranks_df["family"].value_counts().values
# fig, ax = plt.subplots(figsize=(24,7))
# sns.barplot(x,y,ax=ax)
# plt.xticks(rotation=90)
# ax.tick_params(axis = 'x', labelsize = 8)
# ax.set_xlabel("Taxonomic level: family", fontsize=14)
# ax.set_ylabel("Counts", fontsize=14)
# sns.despine()
# plt.show()

Let's check taxonomic diversity encoded in the DB based on lowest taxonomic range assigned to each organism included

In [185]:
# tallied_tax_lvls = tax_ranks_df.iloc[:,2:].apply(lambda s:"__".join(s),axis=1).values

In [211]:
# txls_cont = []
# for txl in tallied_tax_lvls:
#     if("NA" in txl):
#         lwrank = list(filter(lambda s: s!="", txl.replace("NA","").split("__")))[-1]
#         txls_cont.append(lwrank)
#     else:
#         lwrank = list(filter(lambda s: s!="", txl.split("__")))[-1]
#         txls_cont.append(lwrank)

In [221]:
# x = pd.Series(txls_cont).value_counts().index
# y = pd.Series(txls_cont).value_counts().values
# fig, ax = plt.subplots(figsize=(35,12))
# sns.barplot(x,y,ax=ax)
# plt.xticks(rotation=90)
# ax.tick_params(axis = 'x', labelsize = 8)
# ax.tick_params(axis = 'y', labelsize = 18)
# ax.set_xlabel("Lowest taxonomic level", fontsize=30)
# ax.set_ylabel("Counts", fontsize=30)
# sns.despine()
# plt.show()